## Refill with noise contacts

Here we take our binomially downsampled coolers and:

1. Calculate the exact number of contacts they lost from the original
2. Generate a temporary contact map of uniformly randomly sampled ligations or "noise contacts"
3. Merge the downsampled map with the noise map to get a contact map with the same depth as the original (including the injected noise)

In [14]:
import multiprocess as mp
import numpy as np
import pandas as pd
import bioframe
import cooler
from cooltools.api.coverage import coverage

In [11]:
cooler.set_verbosity_level(2)

In [12]:
def generate_noise_pixels(bin_ids, n_contacts, chunksize):
    
    def _generate_chunk(n):
        contacts = pd.DataFrame({
            "bin1_id": np.random.choice(bin_ids, n),
            "bin2_id": np.random.choice(bin_ids, n),
        })
        mask = contacts["bin1_id"] > contacts["bin2_id"]
        tmp = contacts.loc[mask, "bin1_id"].copy()
        contacts.loc[mask, "bin1_id"] = contacts.loc[mask, "bin2_id"].copy()
        contacts.loc[mask, "bin2_id"] = tmp
        pixels = (
            contacts
            .groupby(["bin1_id", "bin2_id"])
            .size()
            .rename("count")
            .reset_index()
        )
        return pixels
    
    while n_contacts > 0:
        n = min(n_contacts, chunksize)
        yield _generate_chunk(n)
        n_contacts -= n

In [18]:
binsize = 50_000
clr = cooler.Cooler(f"/net/projects/hic-atlas/spracklin-et-al-datasets/Unsynchronized.hg38.mapq_30.1000.mcool::resolutions/{binsize}")
n_contacts_total = clr.info["sum"]
with mp.Pool(32) as pool:
    cis_cov, tot_cov = coverage(clr, ignore_diags=2, map=pool.map)
    trs_cov = tot_cov - cis_cov
    


In [8]:
for downsample_perc in [75, 50, 35, 10]:  # 95, 90, 85,
    print(f"Refilling from {downsample_perc}\%")
    clr = cooler.Cooler(f"/net/projects/hic-atlas/test-data/Unsynchronized.hg38.mapq_30.downsample_{downsample_perc}.{binsize}.cool")
    bins = clr.bins()[:]
    good_bin_ids = np.where(tot_cov > 0)[0]

    n_contacts_to_fill = n_contacts_total - clr.info["sum"]
    cooler.create_cooler(
        "/tmp/noise.cool", 
        bins, 
        generate_noise_pixels(good_bin_ids, n_contacts_to_fill, chunksize=50_000_000)
    )
    cooler.merge_coolers(
        f"/net/projects/hic-atlas/test-data/Unsynchronized.hg38.mapq_30.downsample_{downsample_perc}+noise.{binsize}.cool",
        [f"/net/projects/hic-atlas/test-data/Unsynchronized.hg38.mapq_30.downsample_{downsample_perc}.{binsize}.cool", "/tmp/noise.cool"],
        mergebuf=50_000_000
    )
    
    assert cooler.Cooler(
        f"/net/projects/hic-atlas/test-data/Unsynchronized.hg38.mapq_30.downsample_{downsample_perc}+noise.{binsize}.cool"
    ).info["sum"] == n_contacts_total

Refilling from 75\%
Writing chunk 0: /tmp/tmpnbvgeerj.multi.cool::0
Creating cooler at "/tmp/tmpnbvgeerj.multi.cool::/0"
Writing chroms
Writing bins
Writing pixels
writing chunk 0
Writing indexes
Writing info
Writing chunk 1: /tmp/tmpnbvgeerj.multi.cool::1
Creating cooler at "/tmp/tmpnbvgeerj.multi.cool::/1"
Writing chroms
Writing bins
Writing pixels
writing chunk 0
Writing indexes
Writing info
Writing chunk 2: /tmp/tmpnbvgeerj.multi.cool::2
Creating cooler at "/tmp/tmpnbvgeerj.multi.cool::/2"
Writing chroms
Writing bins
Writing pixels
writing chunk 0
Writing indexes
Writing info
Writing chunk 3: /tmp/tmpnbvgeerj.multi.cool::3
Creating cooler at "/tmp/tmpnbvgeerj.multi.cool::/3"
Writing chroms
Writing bins
Writing pixels
writing chunk 0
Writing indexes
Writing info
Writing chunk 4: /tmp/tmpnbvgeerj.multi.cool::4
Creating cooler at "/tmp/tmpnbvgeerj.multi.cool::/4"
Writing chroms
Writing bins
Writing pixels
writing chunk 0
Writing indexes
Writing info
Writing chunk 5: /tmp/tmpnbvgeerj.m

KeyboardInterrupt: 